In [20]:
from datasets import load_dataset
import re

In [23]:
dataset = load_dataset("mozilla-foundation/common_voice_7_0", "fr", split="train", use_auth_token=True)

Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/fr/7.0.0/fe20cac47c166e25b1f096ab661832e3da7cf298ed4a91dcaa1343ad972d175b)


In [24]:
chars_to_ignore_regex = '[^a-zàâäçéèêëîïôöùûüÿ\'’ ]'

def extract_text(batch):
    batch["text"] = re.sub(chars_to_ignore_regex, "", batch["sentence"].lower()).replace('’', "'")
    return batch

dataset = dataset.map(extract_text, remove_columns=["sentence"])

0ex [00:00, ?ex/s]

In [25]:
dataset.push_to_hub(f"common_voice_7_0_fr_processed", split="train")

Pushing dataset shards to the dataset hub:   0%|          | 0/29 [00:00<?, ?it/s]

In [26]:
with open("text_for_lm.txt", "w") as file:
    file.write(" ".join(dataset["text"]))

In [20]:
with open("5gram.arpa", "r") as read_file, open("5gram_correct.arpa", "w") as write_file:
    has_added_eos = False
    for line in read_file:
        if not has_added_eos and "ngram 1=" in line:
            count=line.strip().split("=")[-1]
            write_file.write(line.replace(f"{count}", f"{int(count)+1}"))
        elif not has_added_eos and "<s>" in line:
            write_file.write(line)
            write_file.write(line.replace("<s>", "</s>"))
            has_added_eos = True
        else:
            write_file.write(line)

In [1]:
from transformers import AutoProcessor

In [3]:
processor = AutoProcessor.from_pretrained("./")

In [4]:
vocab_dict = processor.tokenizer.get_vocab()

In [5]:
sorted_vocab_dict = {k.lower(): v for k, v in sorted(vocab_dict.items(), key=lambda item: item[1])}

In [6]:
from pyctcdecode import build_ctcdecoder

decoder = build_ctcdecoder(
    labels=list(sorted_vocab_dict.keys()),
    kenlm_model_path="./language_model/5gram_correct.arpa",
)

Loading the LM will be faster if you build a binary file.
Reading /home/pascal/kenlm/build/bin/xls-r-300m-lm-fr/language_model/5gram_correct.arpa
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
****************************************************************************************************


In [7]:
from transformers import Wav2Vec2ProcessorWithLM

processor_with_lm = Wav2Vec2ProcessorWithLM(
    feature_extractor=processor.feature_extractor,
    tokenizer=processor.tokenizer,
    decoder=decoder
)

In [8]:
processor_with_lm.save_pretrained("xls-r-300m-lm-fr")